In [1]:
%matplotlib osx 

import obspy as op
import numpy as np

from landscapeWithOcean import LandscapeWithOcean

from obspy.clients.fdsn import Client
import matplotlib.pyplot as plt
import os

from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

import csv

from skimage.color import rgb2gray
from skimage import img_as_ubyte

from skimage import io

from matplotlib.animation import FFMpegWriter

In [2]:
with open ('PacificaCoast_DistanceElevation.csv') as csvfile:
    readCSV=csv.reader (csvfile, delimiter=',')
    D=[]
    E=[]
    for row in readCSV:
        D.append(float(row[0]))
        E.append(float(row[1]))
    
#plt.hist(E, 25,range=[6,12])
print(len(E))

500


In [3]:
# (1) Load and display the image
image = io.imread('PacificaCoast250.png')

#plt.axis('on') # turn off axis labels
#plt.imshow(image,cmap='gray')
#plt.show()

In [4]:
image_gray = rgb2gray(image)

#plt.axis('on') # turn off axis labels
#plt.imshow(image_gray,cmap='gray')
#plt.show()

In [5]:
#plt.hist(image_gray.ravel(),bins=256)
#plt.show()

In [6]:
image = io.imread('PacificaCoast250.png')
image_gray = rgb2gray(image)

m = np.mean(E)
n = 250
inc = 0

#integrate elevation data
for i in range(n):
    inc = 0
    for j in range(n):
        if (image_gray[i,j] > .8):
            image_gray[i,j] = 0
        else:
            image_gray[i,j] = E[((n-1)-i)*2] +  m/(E[((n-1)-i)*2])* inc
            inc = inc + .005
            
image_elevation = np.copy(image_gray)

image_elevation = np.flip(np.flip(np.rot90(np.rot90(np.rot90(image_elevation))),axis=1),axis=0)

#give elevation a slope downhill towards coast
for i in range(n):
    for j in range(n):
        if(image_elevation[i,j]==0):
            image_elevation[i,j] = (image_elevation[i-1,j])/1.075
            
            
image_elevation = np.flip(image_elevation,axis=0)

#plt.axis('on') # turn off axis labels
#plt.imshow(image_elevation,cmap='gray')
#plt.show()

In [7]:
### Define simulation grid and initial conditions

NX = 125*2 #number of rows
NY = 125*2 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion
#Z = rand(NX,NY)*0.1
Z=image_elevation
#print(Z)
#print(image_elevation)
#for i in range(5):
 #   xx = .5 * i/10 * NX
  #  yy = .5 * i/10 * NY
   # r  = (0.5*i)*NX
    #h  = (0.5*i)*5
    #Z = AddHill(Z,NX,NY,xx,yy,r,h)

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [8]:
### Physical Parameters
K = 1.0e-6 # meters^(1-2m)/yr

D = 0.005 # m^2/yr

# uplift rate
#uplift = 0.03 / 600.
uplift = 0.0

In [9]:
### Model parameters

# Time step
#dt = d**2 / D / 8. 
dt = d**2 / D /(2.**9) #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10

 dt[years] =  9.765625


In [10]:
# Total simulation time
T = 10000

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of iteration: ',n_iter)

Number of iteration:  1024


In [11]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.1  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           0.001947439613870898
Maximum elevation           11.874836288704088
Beach level                 1.189236324522893
Ocean volume                19753.714475905406
Percentage of ocean surface 32.107200000000006


In [12]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.terrain)
        cs = ax2.contour(ZPlot,6,colors='k', linewidths = .25)

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [13]:
metadata = dict(title='Erosion', artist='Matplotlib',comment='Pacifica')
writer = FFMpegWriter(fps=10, metadata=metadata)

# Set up figure
fig = init_figure()
update_figure()
Znew = np.copy(Z)

with writer.saving(fig, "animation.mp4", dpi=500):
    for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            #iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            #iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.
            iL = np.max([i-1,0])
            iR = np.min([i+1,NX-1])

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            update_figure()
            writer.grab_frame()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')

update_figure()
print(' Simulation finished.')

.........10 Ocean level= 1.1892786523672858  Ocean surface fraction= 32.136
.........20 Ocean level= 1.1892786523672858  Ocean surface fraction= 32.1664
.........30 Ocean level= 1.1892411275080252  Ocean surface fraction= 32.2
.........40 Ocean level= 1.1892411275080252  Ocean surface fraction= 32.2384
.........50 Ocean level= 1.1892411275080252  Ocean surface fraction= 32.264
.........60 Ocean level= 1.1891855279544505  Ocean surface fraction= 32.288
.........70 Ocean level= 1.1891855279544505  Ocean surface fraction= 32.3168
.........80 Ocean level= 1.1891749744669666  Ocean surface fraction= 32.3456
.........90 Ocean level= 1.1891749744669666  Ocean surface fraction= 32.368
.........100 Ocean level= 1.1891749744669666  Ocean surface fraction= 32.3856
.........110 Ocean level= 1.1891749744669666  Ocean surface fraction= 32.4096
.........120 Ocean level= 1.1891749744669666  Ocean surface fraction= 32.4304
.........130 Ocean level= 1.1891624258930364  Ocean surface fraction= 32.4464
..